In [1]:
import pandas as pd
import numpy as np
from sklearn import preprocessing
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
import math

<h1>1. Preprocesamiento</h1>

<h2>1.1 Normalización</h2>

In [2]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [3]:
df_0 = pd.read_csv('Data\Concrete_Data_Yeh.csv')

df_p = preprocessing.normalize(df_0, axis=0)
df = pd.DataFrame(df_p, columns=df_0.columns)
df.describe()

cement         slag       flyash        water  superplasticizer  \
count  1030.000000  1030.000000  1030.000000  1030.000000       1030.000000   
mean      0.029208     0.020274     0.020141     0.030946          0.022451   
std       0.010856     0.023672     0.023786     0.003640          0.021616   
min       0.010596     0.000000     0.000000     0.020759          0.000000   
25%       0.019984     0.000000     0.000000     0.028105          0.000000   
50%       0.028349     0.006036     0.000000     0.031531          0.023158   
75%       0.036359     0.039220     0.043969     0.032724          0.036908   
max       0.056096     0.098607     0.074372     0.042098          0.116515   

       coarseaggregate  fineaggregate          age        csMPa  
count      1030.000000    1030.000000  1030.000000  1030.000000  
mean          0.031060       0.030993     0.018259     0.028241  
std           0.002482       0.003212     0.025260     0.013172  
min           0.025571       0.023798     0.000400     0.001837  
25%           0.029754       0.029285     0.002799     0.018694  
50%           0.030903       0.031230     0.011197     0.027158  
75%           0.032863       0.033013     0.022393     0.036375  
max           0.036554       0.039768     0.145956     0.065126

<h2>1.2 Selección de variables</h2>

<h3>1.2.1 Generación de nuevas variables</h3>

In [4]:
## Generación de realciones

columnas = list(df.drop(columns=['csMPa']).columns)
for i in columnas:
    columnas_2 = [x for x in columnas if x not in i]
    for j in columnas_2:
        nombre_columna = i + '-' + j
        df[nombre_columna] = df[i] / df[j]

## Dejar varibales con valores no indeterminados

df = df[list(df.describe().replace([np.inf, -np.inf], np.nan).iloc[-1].dropna().index)]

## Generación de Exponenciales

columnas = list(df.drop(columns=['csMPa']).columns)

for i in columnas:
    nombre_columna = 'exp_' + i
    df[nombre_columna] = df[i].apply(lambda x: math.exp(x))

D:\Anaconda\lib\site-packages\numpy\lib\function_base.py:3949: RuntimeWarning: invalid value encountered in multiply
  x2 = take(ap, indices_above, axis=axis) * weights_above


<h3>1.2.2 Selección por GA con AIC</h3>

In [5]:
## Definición funcion a optimizar

def aic_criterion(df):
    n_var = len(df.drop(columns=['residuos'
                                 , 'csMPa'
                                 , 'csMPa_est']).columns)
    
    n = len(df)
    
    res = sum(df['residuos'].apply(lambda x: x ** 2))
    
    return((n * (math.log(res / (n - n_var - 1)))) + (2 * n_var))

In [6]:
## Generar población inicial aleatoria

np.random.seed(1984)

explicativas = list(df.drop(columns=['csMPa']).columns)
df_explicativas = pd.DataFrame(np.random.randint(2,size=(500, len(explicativas))), columns=explicativas)
df_explicativas['aic'] = 200000

y = df['csMPa']
aic_col = pd.Series([])

for i in range(len(df_explicativas)):
    X = df[list(df_explicativas.iloc[i][df_explicativas.iloc[i] == 1].index)]
    X_val, X_other, y_val, y_other = train_test_split(X, y, test_size=0.80, random_state=42, shuffle=False)
    X_train, X_test, y_train, y_test = train_test_split(X_other, y_other, test_size=0.40, shuffle=False)

    del X_other
    del y_other
    
    reg = LinearRegression().fit(X_train, y_train)
    y_val_est = pd.Series(reg.predict(X_val))
    
    df_val = pd.concat([X_val, y_val,y_val_est], axis=1).rename(columns={0 : 'csMPa_est'})
    df_val['residuos'] = df_val['csMPa'] - df_val['csMPa_est']
    
    df_explicativas['aic'].iloc[i] = aic_criterion(df_val)

D:\Anaconda\lib\site-packages\ipykernel_launcher.py:10: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  # Remove the CWD from sys.path while we load stuff.
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

...

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, value)
D:\Anaconda\lib\site-packages\pandas\core\indexing.py:671: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_with_indexer(indexer, va

In [7]:
## Generar operadores de cruce y mutacion

def cruce(cromosoma_0, cromosoma_1, tipo_cruce):
    
    rng = np.random.default_rng()
    largo_cromosoma = len(cromosoma_0)
    rango_cromosoma = range(largo_cromosoma)
    
    if tipo_cruce == 'punto unico':
        
        punto = rng.choice(rango_cromosoma, size=1, replace=False)[0]
        
        descendencia_0 = np.concatenate((cromosoma_0[:punto], cromosoma_1[punto:]), axis = 0)
        descendencia_1 = np.concatenate((cromosoma_1[:punto], cromosoma_0[punto:]), axis = 0)
        
        return(descendencia_0, descendencia_1)
    
    elif tipo_cruce == 'dos puntos':
        
        puntos = rng.choice(rango_cromosoma, size=2, replace=False)
        punto_0 = min(puntos[0], puntos[1])
        punto_1 = max(puntos[0], puntos[1])
        
        descendencia_0 = np.concatenate((cromosoma_0[:punto_0]
                                         , cromosoma_1[punto_0:punto_1]
                                         , cromosoma_0[punto_1:]), axis = 0)
        descendencia_1 = np.concatenate((cromosoma_1[:punto_0]
                                         , cromosoma_0[punto_0:punto_1]
                                         , cromosoma_1[punto_1:]), axis = 0)
        
        return(descendencia_0, descendencia_1)
    
    elif tipo_cruce == 'uniforme':

        padre_0 = np.random.randint(2,size=(len(cromosoma_0), 1))
        padre_1 = (padre_0 - 1) * (- 1)
        
        descendencia_0 = [(padre_0[i] * cromosoma_0[i])[0] + (padre_1[i] * cromosoma_1[i])[0] for i in range(len(cromosoma_0))]
        descendencia_1 = [(padre_0[i] * cromosoma_1[i])[0] + (padre_1[i] * cromosoma_0[i])[0] for i in range(len(cromosoma_0))]
        
        return(descendencia_0, descendencia_1)

    
    
def mutacion(cromosoma_0, tipo_dato):
    
    largo_cromosoma = len(cromosoma_0)
    rango_cromosoma = range(largo_cromosoma)
    
    if tipo_dato == 'binario':
        gen_mutacion = rng.choice(rango_cromosoma, size=1, replace=False)[0]
        
        if cromosoma_0[gen_mutacion] == 1:
            nuevo_gen = 0
        else:
            nuevo_gen = 1
        
        cromosoma_0 = np.concatenate((cromosoma_0[:gen_mutacion]
                                      ,np.array([nuevo_gen])
                                      ,cromosoma_0[gen_mutacion+1:]), axis = 0)
        return(cromosoma_0)

In [32]:
## Generar funciones de seleccion

def seleccion(df, tipo_seleccion, tamano_elitismo):
    
    df['dummy'] = 0
    df['seleccionado'] = 0
    
    df = df.sort_values(['aic']).reset_index()
    #df['orden'] = df.sort_values(['aic']).groupby(['dummy']).cumcount()+1
    
    if tipo_seleccion == 'ruleta':
        if tamano_elitismo > 0:
            
            max_aic = max(df['aic'])
            df['aic_escalado'] = (df['aic'] - max_aic - 1) * (-1)
            df['aic_escalado_norm'] = (df['aic_escalado'] - df['aic_escalado'].min()) / (df['aic_escalado'].max() - df['aic_escalado'].min())
            
            total_aic_esc = sum(df['aic_escalado'])
            df['prob'] = df['aic_escalado'] / total_aic_esc
            df['prob'] = df['prob'] / max(df['prob'])
            df['prob_1'] = df['prob'].shift(-1).fillna(0) + 0.000001
            df['espacio'] = (df['prob'] - df['prob_1'])*100
                
        else:
            print('bad')
    elif tipo_seleccion == 'torneo':
        if tamano_elitismo > 0:
            print('bad')
        else:
            print('bad')       

    df = df.drop(columns=['dummy'])
    
    return(df)

In [33]:
seleccion(df_explicativas, 'ruleta', 1)

index  cement  slag  flyash  water  superplasticizer  coarseaggregate  \
0       30       1     0       1      1                 1                1   
1      124       1     1       1      0                 1                0   
2       54       0     1       1      0                 1                0   
3      351       1     1       1      1                 1                1   
4       98       0     0       0      0                 1                0   
5      367       0     0       0      1                 0                0   
6      218       0     1       1      0                 1                0   
7       81       0     1       1      0                 1                0   
8      175       1     1       0      0                 0                0   
9       31       1     0       1      1                 0                1   
10      68       1     0       1      0                 0                1   
11     300       0     0       0      1                 0                0   
12      59       0     1       0      0                 0                0   
13     381       1     0       1      1                 0                1   
14     261       1     1       1      1                 0                0   
15     305       1     0       0      1                 1                1   
16     376       0     1       0      0                 0                0   
17     176       0     0       1      1                 1                0   
18      95       0     1       0      1                 0                1   
19     487       1     1       0      0                 0                1   
20     369       0     0       1      0                 0                0   
21     476       0     1       1      0                 1                0   
22     267       0     1       1      1                 0                1   
23      40       1     0       0      0                 0                1   
24      73       1     1       0      1                 1                1   
25     311       1     0       0      0                 0                0   
26      16       1     0       0      1                 1                1   
27     160       0     0       0      1                 1                1   
28     439       1     0       1      0                 1                0   
29     357       0     1       1      1                 0                0   
30       6       0     0       0      1                 1                1   
31     169       0     0       0      1                 1                0   
32      86       0     0       0      0                 1                1   
33     207       1     1       0      0                 1                0   
34     260       0     0       0      0                 1                1   
35     179       1     1       1      1                 0                1   
36     393       1     0       1      1                 1                1   
37     496       0     0       0      0                 0                1   
38     101       0     0       0      0                 0                0   
39     181       1     0       0      0                 0                1   
40      42       1     0       1      1                 0                0   
41      17       0     0       0      0                 0                0   
42     474       0     0       0      0                 1                0   
43     233       0     0       1      0                 0                0   
44     470       0     0       0      0                 0                0   
45     349       0     0       0      0                 1                0   
46     139       1     1       1      1                 0                0   
47     340       1     0       0      0                 0                1   
48     480       0     0       1      1                 1                0   
49     183       1     1       0      0                 0                0   
50     205       1     1   

In [31]:
df_explicativas

cement  slag  flyash  water  superplasticizer  coarseaggregate  \
0         0     1       1      1                 1                0   
1         0     0       1      1                 0                1   
2         1     0       0      1                 1                1   
3         0     0       0      1                 1                0   
4         0     1       0      1                 1                0   
5         0     1       1      1                 1                1   
6         0     0       0      1                 1                1   
7         0     0       0      1                 0                0   
8         1     1       1      1                 1                0   
9         1     0       0      0                 1                0   
10        1     0       1      0                 0                0   
11        1     0       0      1                 0                0   
12        1     0       0      1                 0                0   
13        1     1       0      0                 0                0   
14        1     1       0      0                 0                1   
15        1     1       0      0                 0                0   
16        1     0       0      1                 1                1   
17        0     0       0      0                 0                0   
18        1     1       0      0                 0                0   
19        1     1       0      0                 0                1   
20        1     1       1      0                 0                1   
21        0     0       0      1                 0                1   
22        1     0       0      1                 0                0   
23        1     1       0      1                 0                0   
24        1     0       0      0                 1                0   
25        0     1       1      0                 1                0   
26        1     1       0      1                 1                0   
27        1     1       0      0                 1                1   
28        0     1       1      1                 0                0   
29        1     1       1      1                 0                1   
30        1     0       1      1                 1                1   
31        1     0       1      1                 0                1   
32        1     1       1      0                 0                1   
33        1     0       1      0                 0                0   
34        0     1       1      0                 1                1   
35        1     0       1      1                 0                1   
36        1     1       1      0                 1                0   
37        0     0       0      0                 0                1   
38        0     1       0      0                 1                1   
39        0     0       1      0                 0                1   
40        1     0       0      0                 0                1   
41        0     0       0      1                 1                1   
42        1     0       1      1                 0                0   
43        1     0       1      0                 1                0   
44        0     0       1      0                 1                1   
45        0     0       1      0                 1                0   
46        1     1       0      1                 0                1   
47        1     1       1      1                 0                1   
48        1     1       0      0                 0                0   
49        0     0       0      0                 0                0   
50        0     1       1      0                 1                1   
51        0     1       0      1                 1                1   
52        1     0       1      1                 1                1   
53        1     1       0      1                 1                0   
54        0     1       1      0                 1                0   
55        0     1       1    

In [30]:
preprocessing.normalize(df_explicativas, axis=0)

array([[ 0.        ,  0.06274558,  0.06362848, ..., -0.04472136,
        -0.04472136, -0.04472136],
       [ 0.        ,  0.        ,  0.06362848, ..., -0.04472136,
        -0.04472136, -0.04472136],
       [ 0.06131393,  0.        ,  0.        , ..., -0.04472136,
        -0.04472136, -0.04472136],
       ...,
       [ 0.06131393,  0.        ,  0.        , ..., -0.04472136,
        -0.04472136, -0.04472136],
       [ 0.06131393,  0.        ,  0.        , ..., -0.04472136,
        -0.04472136, -0.04472136],
       [ 0.06131393,  0.        ,  0.06362848, ..., -0.04472136,
        -0.04472136, -0.04472136]])